# Encontro 12: Algoritmo de Girvan-Newman

Importando a biblioteca:

Configurando a biblioteca:

In [101]:
import sys
sys.path.append('..')

import old_socnet as sn

In [119]:
sn.graph_width = 400
sn.graph_height = 225

sn.edge_width = 1

Carregando o primeiro grafo:

In [131]:
g = sn.load_graph('teste.gml', has_pos=True)

sn.show_graph(g)

Você pode usar esse grafo para depurar sua implementação do cálculo de *edge betweenness*.

In [134]:
def calculate_partial_betweenness(g, s):
    import math
    import queue
    
    for n,m in g.edges_iter():
        g.edge[n][m]['partial_betweenness'] = 0
        
    for n in g.nodes():
        g.node[n]['n_geodesics'] = 0
        g.node[n]['fluid_value'] = 1
        g.node[n]['distance'] = math.inf
        g.node[n]['neighbors_geodesic'] = []
        g.node[n]['parents'] = []
        
    g.node[s]['n_geodesics'] = 1
    g.node[s]['distance'] = 0
    
    nodes_distance = queue.Queue()
    nodes_distance.put(s)
    
    visited_nodes_distance = set(nodes_distance.queue)
    
    #Busca em largura
    while not nodes_distance.empty():
        y = nodes_distance.get()
        for n in g.neighbors(y):
            if (g.node[n]['distance'] > g.node[y]['distance']):
                if (y not in g.node[n]['parents']):
                    g.node[n]['parents'].append(y)
                if (n not in g.node[y]['neighbors_geodesic']):
                        g.node[y]['neighbors_geodesic'].append(n)
                if (n not in visited_nodes_distance):
                    nodes_distance.put(n)
                    visited_nodes_distance.add(n)
                g.node[n]['distance'] = g.node[y]['distance'] + 1
    #########
   
    #Calculo distancia máxima      
    aux = 0
    for n in g.nodes():
        if g.node[n]['distance'] > aux and not math.isinf(g.node[n]['distance']):
            aux = g.node[n]['distance']
    #######

    
    #### Lista dos nos mais profundos

    last_nodes = queue.Queue()
    
    for n in g.nodes():
        if g.node[n]['distance'] == aux:
            last_nodes.put(n)
    ########

    
    #### Busca em largura pelos nós das geodesicas
    nodes_n_geodesics = queue.Queue()
    nodes_n_geodesics.put(s)
    vistied_nodes_geodesics = set(nodes_n_geodesics.queue)
    
    while not nodes_n_geodesics.empty():
        x = nodes_n_geodesics.get()
        for i in g.node[x]['parents']:
            g.node[x]['n_geodesics'] += g.node[i]['n_geodesics']
        for i in g.node[x]['neighbors_geodesic']:
            if i not in vistied_nodes_geodesics:
                vistied_nodes_geodesics.add(i)
                nodes_n_geodesics.put(i)
    ######
    
    fluid_visited_nodes = set(last_nodes.queue)
    while not last_nodes.empty():
        x = last_nodes.get()
        for i in g.node[x]['parents']:
            g.edge[i][x]['partial_betweenness'] = (g.node[i]['n_geodesics'] / g.node[x]['n_geodesics']) * g.node[x]['fluid_value']
            g.node[i]['fluid_value'] += g.edge[i][x]['partial_betweenness']
            if i not in fluid_visited_nodes:
                last_nodes.put(i)
                fluid_visited_nodes.add(i)
#     for n,m in g.edges_iter():
#         print(n,m, g.edge[n][m])


In [135]:
calculate_partial_betweenness(g,0)

Carregando o segundo grafo:

In [136]:
sn.graph_width = 800
sn.graph_height = 450

g = sn.load_graph('karate.gml', has_pos=True)

sn.show_graph(g)

Construindo uma animação do Girvan-Newman:

In [137]:
from random import randrange
from queue import Queue


def snapshot(g, frames):
    frame = sn.generate_frame(g)

    frames.append(frame)


frames = []

prev_num_components = 1

gc = g.copy()

snapshot(gc, frames)

while g.edges():
    # Identifica e remove a aresta com maior betweenness.

    for n, m in g.edges():
        g.edge[n][m]['betweenness'] = 0

    for n in g.nodes():
        calculate_partial_betweenness(g, n)

        for n, m in g.edges():
            g.edge[n][m]['betweenness'] += g.edge[n][m]['partial_betweenness']

    for n, m in g.edges():
        g.edge[n][m]['betweenness'] /= 2

    n, m = max(g.edges(), key=lambda e: g.edge[e[0]][e[1]]['betweenness'])

    g.remove_edge(n, m)

    gc.edge[n][m]['color'] = (255, 255, 255)

    # Calcula o número de componentes depois da remoção.

    for n in g.nodes():
        g.node[n]['label'] = 0

    label = 0
    q = Queue()

    for s in g.nodes():
        if g.node[s]['label'] == 0:
            label += 1

            g.node[s]['label'] = label
            q.put(s)

            while not q.empty():
                n = q.get()

                for m in g.neighbors(n):
                    if g.node[m]['label'] == 0:
                        g.node[m]['label'] = label
                        q.put(m)

    num_components = label

    # Se o número de componentes aumentou, identifica as componentes por cores aleatórias.

    if prev_num_components < num_components:
        colors = {}

        for label in range(1, num_components + 1):
            colors[label] = (randrange(256), randrange(256), randrange(256))

        for n in gc.nodes():
            gc.node[n]['color'] = colors[g.node[n]['label']]

        prev_num_components = num_components

    snapshot(gc, frames)

sn.show_animation(frames)

Você não precisa modificar esse código, apenas completar o código de `calculate_partial_betweenness`.

O "gabarito" deste notebook é o vídeo `encontro12.webm` que está na mesma pasta.